# Climate-Friendly Food Systems (CFFS) Labelling Project

### The University of British Columbia

#### Created by Silvia Huang, CFFS Data Analyst
***

## Part III: Update Information and Mapping

# Climate-Friendly Food Systems (CFFS) Labelling Project

### The University of British Columbia

#### Created by Silvia Huang, CFFS Data Analyst
***

## Part III: Update Information and Mapping

## Set up and Import Libraries

In [1]:
#pip install -r requirements.txt

In [2]:
import numpy as np
import pandas as pd
import pdpipe as pdp
import matplotlib.pyplot as plt
import glob
import os
import csv
from itertools import islice
from decimal import Decimal
import xml.etree.ElementTree as et
from xml.etree.ElementTree import parse
import openpyxl
import pytest
from datetime import datetime

/Users/jennylee/opt/anaconda3/lib/python3.9/site-packages/pdpipe/col_generation.py:12: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm


In [3]:
# Set the root path, change the the current working directory into the project folder
path = os.getcwd()
os.chdir(path)

In [4]:
# Enable reading data table in the scrolling window if you prefer
pd.set_option("display.max_rows", None, "display.max_columns", None)

***
## Import Preprocessed Datasets

In [5]:
Preps = pd.read_csv(os.path.join(os.getcwd(), "data", "cleaning", "Preps_Unit_Cleaned.csv"))
Preps.head()

PrepId                    Description  PakQty PakUOM InventoryGroup  \
0  P-27317   BATCH|3 Bean Vegetable Chili   21.00     Kg           PREP   
1  P-56699  BATCH|Cauliflower Wings|Baked    1.00     Kg            NaN   
2  P-64163     Batch|Chicken Burger|Shoyu    7.65     Kg           PREP   
3  P-26333        BATCH|Citrus Herb Aioli    3.00      L           PREP   
4  P-53598             BATCH|Coleslaw mix    1.50     Kg            NaN   

    StdQty StdUom  
0  21000.0      g  
1   1000.0      g  
2   7650.0      g  
3   3000.0     ml  
4   1500.0      g

In [6]:
ghge_factors = pd.read_csv(os.path.join(os.getcwd(), "data", "external", "ghge_factors.csv"))
ghge_factors.head()

Category ID              Food Category  \
0            1        beef & buffalo meat   
1            2    lamb/mutton & goat meat   
2            3            pork (pig meat)   
3            4  poultry (chicken, turkey)   
4            5                     butter   

   Active Total Supply Chain Emissions (kg CO2 / kg food)  
0                                            41.3463       
1                                            41.6211       
2                                             9.8315       
3                                             4.3996       
4                                            11.4316

In [7]:
nitro_factors = pd.read_csv(os.path.join(os.getcwd(), "data", "external", "nitrogen_factors.csv"))
nitro_factors.head()

Category ID              Food Category  g N lost/kg product
0            1        beef & buffalo meat               329.50
1            2    lamb/mutton & goat meat               231.15
2            3            pork (pig meat)               132.80
3            4  poultry (chicken, turkey)               116.80
4            5                     butter               100.35

In [8]:
water_factors = pd.read_csv(os.path.join(os.getcwd(), "data", "external", "water_factors.csv"))
water_factors.head()

Category ID              Food Category  Freshwater Withdrawals (L/FU)  \
0            1        beef & buffalo meat                       1677.200   
1            2    lamb/mutton & goat meat                        461.200   
2            3            pork (pig meat)                       1810.300   
3            4  poultry (chicken, turkey)                        370.300   
4            5                     butter                       1010.176   

   Stress-Weighted Water Use (L/FU)  
0                         61309.000  
1                           258.900  
2                         54242.700  
3                           333.500  
4                         50055.168

In [9]:
# Load current Items List with assigned Emission Factors Category ID
Items_Assigned = pd.read_csv(os.path.join(os.getcwd(), "data", "mapping", "Items_List_Assigned.csv"))
Items_Assigned.head()

ItemId  CategoryID               Description  CaseQty CaseUOM  PakQty  \
0  I-57545         1.0   CHUCK FLAT BONELESS FZN     3.30      Kg     1.0   
1  I-10869         1.0       BEEF STIRFRY COV FR     5.00      Kg     1.0   
2   I-7064         1.0     BEEF OUTSIDE FLAT AAA     1.00      Kg     1.0   
3  I-37005         1.0            BEEF MEATBALLS     4.54      Kg  1000.0   
4  I-37002         1.0  BEEF INSIDE ROUND SHAVED     9.00      Kg  1000.0   

  PakUOM InventoryGroup  
0     Kg           MEAT  
1     Kg           MEAT  
2     Kg           MEAT  
3      g           MEAT  
4      g           MEAT

In [10]:
new_items = pd.read_csv("data/mapping/new items added/New_Items_Added_11.csv")
new_items

ItemId  CategoryID                  Description  CaseQty CaseUOM  PakQty  \
0   I-68718          24  BUN HAMBURGER WW VEGAN 85GR      1.0    each       1   
1   I-68700          11    EGG CKD FOLDED  VEGAN FRZ     60.0    each       1   
2   I-54711           6   CHEESE HALLOUMI TRE STELLE      6.0     pak     160   
3    I-4757          39                  ONIONS RED      25.0      lb       1   
4   I-36794          25         RICE BASMATI INDIAN       1.0      ea      40   
5    I-3582          54       SEASONING MONTREAL STK      3.4      Kg       1   
6   I-65714          58       CHUTNEY MANGO-TAMARIND      2.0      un    2268   
7   I-19462          58              SAUCE SOY SWEET      4.0     JUG    4300   
8   I-30167          41      SWEET POTATO DICED 1/4"      5.0      lb       1   
9   I-11549          35           CARROTS ORANGE UBC      1.0      lb       1   
10  I-19464          25      NOODLES RICE VERMICELLI     30.0     pak     400   
11   I-3701          19           NUT 1KG PISTACHIO       1.0      Kg       1   
12  I-29755          18       PEAS GREEN WASABI BULK   5000.0       g       1   
13   I-4524          38                 BEETS GOLDBC      5.0      lb       1   
14   I-1271          24    LOAF MARBLE RYE SANDWICH       4.0    LOAF       1   

   PakUOM  InventoryGroup  
0    each           BREAD  
1    each           DAIRY  
2       g           DAIRY  
3      lb         PRODUCE  
4      lb  FOOD - GROCERY  
5      Kg          SPICES  
6       g  FOOD - GROCERY  
7      ml  FOOD - GROCERY  
8      lb         PRODUCE  
9      lb         PRODUCE  
10      g  FOOD - GROCERY  
11     Kg  FOOD - GROCERY  
12      g  CANDIES SNACKS  
13     lb         PRODUCE  
14   LOAF           BREAD

In [11]:
item_nonstd = pd.read_csv("data/cleaning/Items_Nonstd.csv")
item_nonstd

Empty DataFrame
Columns: [IngredientId, Qty, Uom, Conversion, InvFactor, Recipe]
Index: []

In [12]:
preps_nonstd = pd.read_csv("data/cleaning/Preps_NonstdUom.csv")
preps_nonstd

Empty DataFrame
Columns: [PrepId, Description, PakQty, PakUOM, InventoryGroup, StdQty, StdUom]
Index: []

In [13]:
conv_updatecov = pd.read_csv("data/cleaning/update/Conv_UpdateConv.csv")
conv_updatecov

ConversionId  Multiplier  ConvertFromQty ConvertFromUom  ConvertToQty  \
0         I-1028    0.008333           1.000             CT      120.0000   
1         I-1034    0.008333           1.000             CT      120.0000   
2         I-1035    0.010000           1.000             CT      100.0000   
3        I-10605    0.008850           1.000             CT      113.0000   
4         I-1126    0.006667           1.000             CT      150.0000   
5         I-1127    0.006667           1.000             CT      150.0000   
6         I-1141    0.013333           1.000             CT       75.0000   
7         I-1143    0.013333           1.000             CT       75.0000   
8        I-11519    0.020000           1.000            bag       50.0000   
9         I-1152    0.013333           1.000             CT       75.0000   
10       I-11842    0.002203           1.000           LOAF      454.0000   
11        I-1207    0.008333           1.000             CT      120.0000   
12        I-1223    0.000100           1.000             CT    10000.0000   
13        I-1232    0.020000           1.000          slice       50.0000   
14        I-1252    0.000250           1.000             CT     4000.0000   
15        I-1254    0.004167           0.500             CT      120.0000   
16        I-1257    0.008333           1.000             CT      120.0000   
17        I-1273    0.002203           1.000           LOAF      454.0000   
18       I-13004    0.002203           1.000             CT      454.0000   
19       I-15032    0.002203           1.000           LOAF      454.0000   
20       I-15358    0.013333           1.000             ea       75.0000   
21       I-17615    0.071429           1.000          slice       14.0000   
22       I-17617    0.071429           1.000          slice       14.0000   
23       I-17686    0.013333           1.000             ea       75.0000   
24       I-18089    0.008333           1.000             ea      120.0000   
25       I-18915    0.033333           1.000             ea       30.0000   
26       I-19735    0.008333           1.000             CT      120.0000   
27        I-2159    0.020000           1.000             CT       50.0000   
28        I-2281    0.000117           0.076           650G      650.0000   
29        I-2306    0.050000           1.000          slice       20.0000   
30        I-2310    0.050000           1.000          slice       20.0000   
31       I-24227    0.002203           1.000           LOAF      454.0000   
32        I-2586    0.008333           1.000             CT      120.0000   
33        I-2669    0.000862           0.125            PIE      145.0000   
34       I-28899    0.040000           1.000           each       25.0000   
35       I-28904    0.033333           1.000           each       30.0000   
36       I-28907    0.025000           1.000           each       40.0000   
37       I-28920    0.005882           1.000           each      170.0000   
38       I-29663    0.036364           1.000             ea       27.5000   
39       I-29665    0.025000           1.000           each       40.0000   
40       I-29688    0.008333           1.000             ea      120.0000   
41       I-30178    0.008333           1.000          SHEET      120.0000   
42        I-3103    0.033333           1.000             CT       30.0000   
43        I-3143    0.000352           1.000            can     2840.0000   
44       I-32258    0.020000           1.000             ea       50.0000   
45       I-32263    0.033333           1.000             ea       30.0000   
46       I-32268    0.020000           1.000             ea       50.0000   
47        I-3387    0.001000           1.000              L     1000.0000   
48        I-3676    0.000352           1.000         LG CAN     2840.0000   
49        I-3688    0.008333           1.000             CT      120.0000   
50        I-3738    0.003030           1.000          330ML      330.0000   


In [14]:
conv_updatecov.loc[conv_updatecov["ConversionId"] == "P-54581"]

Empty DataFrame
Columns: [ConversionId, Multiplier, ConvertFromQty, ConvertFromUom, ConvertToQty, ConvertToUom]
Index: []

In [15]:
Preps.loc[Preps["PrepId"] == "P-54581"]

Empty DataFrame
Columns: [PrepId, Description, PakQty, PakUOM, InventoryGroup, StdQty, StdUom]
Index: []

***
## Import Update Info

In [16]:
# Import list of prep that need convert uom to standard uom manually
Manual_PrepU = pd.read_csv(os.path.join(os.getcwd(), "data", "cleaning", "update", "Preps_UpdateUom.csv"))
Manual_PrepU.head()

PrepId                 Description  PakQty PakUOM InventoryGroup   StdQty  \
0  P-54697             LEMON|Wedge 1/8     8.0   each           PREP     84.0   
1  P-35132  MARINATED|Lemon & Herb Chx   185.0     ea           PREP  24050.0   
2  P-51992   YIELD|Bread|Sourdough 5/8    36.0  slice            NaN   1620.0   
3  P-26234  BATCH|Roasted Garlic Bread    16.0     ea           PREP   1280.0   
4  P-26170           GRILLED|NaanBread     1.0     ea           PREP    125.0   

  StdUom  
0      g  
1      g  
2      g  
3      g  
4      g

In [17]:
Manual_PrepU.loc[Manual_PrepU["PrepId"] == "P-54581"]

PrepId             Description  PakQty PakUOM InventoryGroup  StdQty  \
212  P-54581  SLICE|Multigrain Bread    22.0  slice            NaN    38.0   

    StdUom  
212      g

In [18]:
# Select the file path for new items list with category id
New_Items_Added = pd.read_csv(os.path.join(os.getcwd(), "data", "mapping", "new items added", "New_Items_Added_10.csv"))
New_Items_Added.tail(15)

ItemId  CategoryID                     Description  CaseQty CaseUOM  \
34  I-64877           3    TMRW SAUSAGE BREAKFAST PATTY      100    each   
35  I-55331           4  CHICK BREAST BL/SO HAL TENDOUT        1      Kg   
36   I-3999           4           CHICK DRUMSTICK HALAL        1      Kg   
37   I-4465          36            ASPARAGUS (LARGE) MX       11      lb   
38  I-22443          40             BAMBOO SHOOTS STRIP        6  LG CAN   
39  I-10616          17                   BEANS ROMANO         1      lb   
40   I-4582          38         CARROTS BABY BUNCHED BC        1    each   
41  I-11670          40     COLESLAW MIX CABBAGE&CARROT        5      lb   
42  I-10265          37            TOMATOES HEIRLOOM BC        1      lb   
43   I-4849          36               SALAD MIX ARTISAN        3     bag   
44  I-62863          59   CK|G&G|HMR|Meat Ball & Pasta.        1      ea   
45  I-19923          12            HALIBUT STEAK 4OZ.OW        1      lb   
46   I-8105          12              SAL LOX SMK SLC OW        1      lb   
47   I-3094          54         PEPPERCORN BLACK WHOLE         3      Kg   
48  I-16060          54                    SUMAC GROUND        1    each   

    PakQty PakUOM   InventoryGroup  
34    1.00     ea             MEAT  
35    1.00     Kg          POULTRY  
36    1.00     Kg          POULTRY  
37    1.00     lb          PRODUCE  
38    2.84      L          PRODUCE  
39    1.00     lb          PRODUCE  
40    1.00     CT          PRODUCE  
41    1.00     lb          PRODUCE  
42    1.00     lb          PRODUCE  
43    2.00     lb          PRODUCE  
44    1.00     ea  PRODUCTION FOOD  
45    1.00     lb          SEAFOOD  
46    1.00     lb          SEAFOOD  
47    1.00     Kg           SPICES  
48  454.00      g           SPICES

In [19]:
# Import list of items that adjusted GHGe factor manually
Manual_Factor = pd.read_csv(os.path.join(os.getcwd(), "data", "mapping", "Manual_Adjust_Factors.csv"))
Manual_Factor.head()

ItemId  CategoryID                   Description  CaseQty CaseUOM  PakQty  \
0  I-52090          59  BURGER BEEF & MUSHROOM HALAL      1.0      cs   48.00   
1  I-45558          59           Prep-Vegan Parmesan   1000.0       g    1.00   
2   I-3352          59        MAYONNAISE PAIL TFC 4L      2.0    each    4.00   
3   I-3223          59  COCONUT MILK 17/19% MILK FAT      6.0  LG CAN    2.84   
4   I-2898          59      MUSTARD DIJON WINE FLEUR      6.0     jar    1.00   

  PakUOM   InventoryGroup  \
0     CT             MEAT   
1      g  PRODUCTION FOOD   
2      L   FOOD - GROCERY   
3      L   FOOD - GROCERY   
4     Kg   FOOD - GROCERY   

   Active Total Supply Chain Emissions (kg CO2 / kg food)  \
0                                           25.00894        
1                                            3.85686        
2                                            3.55000        
3                                            3.50000        
4                                            3.32600        

   g N lost/kg product  Freshwater Withdrawals (L/FU)  \
0               200.86                        1038.84   
1                 0.00                           0.00   
2                 0.00                           0.00   
3                 0.00                           1.00   
4                 0.00                           0.00   

   Stress-Weighted Water Use (L/FU)  
0                           37961.2  
1                               0.0  
2                               0.0  
3                               1.0  
4                               0.0

### Update Correct Uom for Preps

In [20]:
# Update prep list with manully adjusted uom
for index, row in Manual_PrepU.iterrows():
    PrepId = Manual_PrepU.loc[index, 'PrepId']
    qty = Manual_PrepU.loc[index, 'StdQty']
    uom = Manual_PrepU.loc[index, 'StdUom']
    Preps.loc[Preps['PrepId'] == PrepId, 'StdQty'] = qty
    Preps.loc[Preps['PrepId'] == PrepId, 'StdUom'] = uom

In [21]:
Preps.drop_duplicates(subset=['PrepId'], inplace=True,)

In [22]:
Preps.head()

PrepId                    Description  PakQty PakUOM InventoryGroup  \
0  P-27317   BATCH|3 Bean Vegetable Chili   21.00     Kg           PREP   
1  P-56699  BATCH|Cauliflower Wings|Baked    1.00     Kg            NaN   
2  P-64163     Batch|Chicken Burger|Shoyu    7.65     Kg           PREP   
3  P-26333        BATCH|Citrus Herb Aioli    3.00      L           PREP   
4  P-53598             BATCH|Coleslaw mix    1.50     Kg            NaN   

    StdQty StdUom  
0  21000.0      g  
1   1000.0      g  
2   7650.0      g  
3   3000.0     ml  
4   1500.0      g

In [23]:
Preps.shape

(742, 7)

In [24]:
path = os.path.join(os.getcwd(), "data", "cleaning", "Preps_List_Cleaned.csv")
Preps.to_csv(path, index = False, header = True)

In [25]:
Items_Assigned.head()

ItemId  CategoryID               Description  CaseQty CaseUOM  PakQty  \
0  I-57545         1.0   CHUCK FLAT BONELESS FZN     3.30      Kg     1.0   
1  I-10869         1.0       BEEF STIRFRY COV FR     5.00      Kg     1.0   
2   I-7064         1.0     BEEF OUTSIDE FLAT AAA     1.00      Kg     1.0   
3  I-37005         1.0            BEEF MEATBALLS     4.54      Kg  1000.0   
4  I-37002         1.0  BEEF INSIDE ROUND SHAVED     9.00      Kg  1000.0   

  PakUOM InventoryGroup  
0     Kg           MEAT  
1     Kg           MEAT  
2     Kg           MEAT  
3      g           MEAT  
4      g           MEAT

In [26]:
New_Items_Added.head()

ItemId  CategoryID                     Description  CaseQty CaseUOM  \
0  I-13791          24      BAR GF NANAIMO 3X3 WRAPPED       12      CT   
1  I-63679          24                BUTTERHORNS EACH        1      ea   
2  I-31545          24          CAKE CARROT CARM STACK       48   slice   
3   I-1057          24  CAKE CHOC TRIPLE TIGER 12X16IN        2   SHEET   
4  I-60871          24   CAKE SHEET CHOC LAYER 12X16IN        2   SHEET   

   PakQty PakUOM InventoryGroup  
0     1.0     CT    BAKED GOODS  
1     1.0     ea    BAKED GOODS  
2     1.0  slice    BAKED GOODS  
3     1.0  SHEET    BAKED GOODS  
4     1.0  SHEET    BAKED GOODS

### Import List of New Items with Emission Factors Category ID Assigned

In [27]:
frames = [Items_Assigned, New_Items_Added]
Items_Assigned_Updated = pd.concat(frames).reset_index(drop=True, inplace=False).drop_duplicates()
Items_Assigned_Updated.head()

ItemId  CategoryID               Description  CaseQty CaseUOM  PakQty  \
0  I-57545         1.0   CHUCK FLAT BONELESS FZN     3.30      Kg     1.0   
1  I-10869         1.0       BEEF STIRFRY COV FR     5.00      Kg     1.0   
2   I-7064         1.0     BEEF OUTSIDE FLAT AAA     1.00      Kg     1.0   
3  I-37005         1.0            BEEF MEATBALLS     4.54      Kg  1000.0   
4  I-37002         1.0  BEEF INSIDE ROUND SHAVED     9.00      Kg  1000.0   

  PakUOM InventoryGroup  
0     Kg           MEAT  
1     Kg           MEAT  
2     Kg           MEAT  
3      g           MEAT  
4      g           MEAT

In [28]:
Items_Assigned_Updated

ItemId  CategoryID                     Description    CaseQty  \
0       I-57545         1.0         CHUCK FLAT BONELESS FZN      3.300   
1       I-10869         1.0             BEEF STIRFRY COV FR      5.000   
2        I-7064         1.0           BEEF OUTSIDE FLAT AAA      1.000   
3       I-37005         1.0                  BEEF MEATBALLS      4.540   
4       I-37002         1.0        BEEF INSIDE ROUND SHAVED      9.000   
5        I-3876         1.0           BEEF CHUCK GROUND AAA      1.000   
6       I-34065         1.0           BEEF BONES KNUCKLE FZ      1.000   
7       I-11661         1.0           BEEF STEW 3/4" FROZEN      5.000   
8        I-3837         1.0          BEEF STEW DICED 3/4"FR      1.000   
9       I-43648         1.0       BRISKET BEEF CORN SMKD FR      4.500   
10       I-3838         1.0      BEEF BRISKET BNLS 3/4" AAA      1.000   
11      I-49128         1.0       HOT DOG BEEF G/FREE 6 INC     10.000   
12      I-17055         1.0   BEEF RIB BRAISING 3 BONE 1/4"      1.000   
13      I-10775         1.0       HOT DOG BEEF 8IN 4/LB FZN     10.000   
14      I-17671         1.0    BEEF RIB-EYE SHAVED 1.5MM FZ      1.000   
15      I-20879         1.0       SOUVLAKI BEEF 75G SKEWERS      1.000   
16       I-3842         1.0          BEEF INSIDE ROUND AAA       1.000   
17       I-3846         1.0        BEEF LEAN GRD COMMERCIAL      5.000   
18       I-3867         1.0        BEEF STIRFRY MEAT FZ 1ST      5.000   
19       I-9454         1.0         BEEF BACK RIB UT COV FZ      1.000   
20      I-26667         1.0          BURGER PRIME RIB  6OZ      30.000   
21      I-28697         1.0               BURGER QUINOA YAM     60.000   
22      I-47440         1.0             JAMAICAN PATTY MILD     36.000   
23      I-47441         1.0            JAMAICAN PATTY SPICY     36.000   
24      I-13425         2.0    LAMB LEG BNLS COMMODITY AUST      1.000   
25       I-3843         2.0                      LAMB GRDFR      1.000   
26      I-43653         2.0                  LAMB STEW 3/4"     25.000   
27      I-13303         3.0            SAUSAGE PATTIES PORK      5.000   
28      I-11922         3.0       SAUSAGE MEAT CHORIZO FRZN      5.000   
29      I-50575         3.0    SAUSAGE ITAL CRUMBLE CKD FRZ      2.000   
30       I-2317         3.0    SAUSAGE FARMER DOUBLE SMOKED      1.000   
31      I-17667         3.0            SAUSAGE CHORIZO MEAT      5.000   
32       I-2333         3.0   PROSCIUTTO SLICED SAN DANIELE      1.000   
33       I-6869         3.0  PROSCIUTTO COTTO MASTRO SLICED      1.000   
34       I-3856         3.0      PORK LOIN BNLS S/CUT COVFR      1.000   
35       I-3887         3.0       PORK GROUND BRITCO PER KG      1.000   
36       I-3855         3.0                   PORK GRD FRZ       5.000   
37       I-3851         3.0       PORK BUTT BNLS 1/4 COV FR      1.000   
38       I-2311         3.0            HAM PROSCIUTTO BNLS       1.000   
39       I-2310         3.0                      HAM HONEY       6.000   
40       I-2306         3.0            HAM BLACK FOREST slc      6.000   
41       I-8260         3.0       CAPICOLLO EXT HOT CAPOLLA      1.000   
42      I-27410         3.0        BACON 3MM NATURALLY SMKD      5.000   
43       I-2308         3.0                 HAM CAPICOLLIFR      1.000   
44       I-2305         3.0                  BACON PANCETTA      1.000   
45      I-13423         3.0                   PORK STIR FRY      5.000   
46      I-19657         3.0               SAUSAGE ANDOUILLE      5.000   
47       I-2319         3.0         SMOKIES 5.5 CT BAVARIAN      1.000   
48      I-42350         3.0       PORK BACK RIB 1/2 RACK FZ      1.000   
49       I-3853         3.0              PORK CHOP 170G C/C     28.000   
50       I-8140         3.0            SAUSAGE CHORIZO WINE      1.000   
51      I-57497         3.0  SAUSAGE FRANKFURTER FLD ROAST      12.000   
52      I-22916         3.0             PORK BELLY SKON COV      1.000   
53      I-574

In [29]:
Items_Assigned_Updated.shape

(2077, 8)

In [30]:
Items_Assigned_Updated[['CategoryID']] = Items_Assigned_Updated[['CategoryID']].apply(pd.to_numeric)

In [31]:
Items_Assigned_Updated

ItemId  CategoryID                     Description    CaseQty  \
0       I-57545         1.0         CHUCK FLAT BONELESS FZN      3.300   
1       I-10869         1.0             BEEF STIRFRY COV FR      5.000   
2        I-7064         1.0           BEEF OUTSIDE FLAT AAA      1.000   
3       I-37005         1.0                  BEEF MEATBALLS      4.540   
4       I-37002         1.0        BEEF INSIDE ROUND SHAVED      9.000   
5        I-3876         1.0           BEEF CHUCK GROUND AAA      1.000   
6       I-34065         1.0           BEEF BONES KNUCKLE FZ      1.000   
7       I-11661         1.0           BEEF STEW 3/4" FROZEN      5.000   
8        I-3837         1.0          BEEF STEW DICED 3/4"FR      1.000   
9       I-43648         1.0       BRISKET BEEF CORN SMKD FR      4.500   
10       I-3838         1.0      BEEF BRISKET BNLS 3/4" AAA      1.000   
11      I-49128         1.0       HOT DOG BEEF G/FREE 6 INC     10.000   
12      I-17055         1.0   BEEF RIB BRAISING 3 BONE 1/4"      1.000   
13      I-10775         1.0       HOT DOG BEEF 8IN 4/LB FZN     10.000   
14      I-17671         1.0    BEEF RIB-EYE SHAVED 1.5MM FZ      1.000   
15      I-20879         1.0       SOUVLAKI BEEF 75G SKEWERS      1.000   
16       I-3842         1.0          BEEF INSIDE ROUND AAA       1.000   
17       I-3846         1.0        BEEF LEAN GRD COMMERCIAL      5.000   
18       I-3867         1.0        BEEF STIRFRY MEAT FZ 1ST      5.000   
19       I-9454         1.0         BEEF BACK RIB UT COV FZ      1.000   
20      I-26667         1.0          BURGER PRIME RIB  6OZ      30.000   
21      I-28697         1.0               BURGER QUINOA YAM     60.000   
22      I-47440         1.0             JAMAICAN PATTY MILD     36.000   
23      I-47441         1.0            JAMAICAN PATTY SPICY     36.000   
24      I-13425         2.0    LAMB LEG BNLS COMMODITY AUST      1.000   
25       I-3843         2.0                      LAMB GRDFR      1.000   
26      I-43653         2.0                  LAMB STEW 3/4"     25.000   
27      I-13303         3.0            SAUSAGE PATTIES PORK      5.000   
28      I-11922         3.0       SAUSAGE MEAT CHORIZO FRZN      5.000   
29      I-50575         3.0    SAUSAGE ITAL CRUMBLE CKD FRZ      2.000   
30       I-2317         3.0    SAUSAGE FARMER DOUBLE SMOKED      1.000   
31      I-17667         3.0            SAUSAGE CHORIZO MEAT      5.000   
32       I-2333         3.0   PROSCIUTTO SLICED SAN DANIELE      1.000   
33       I-6869         3.0  PROSCIUTTO COTTO MASTRO SLICED      1.000   
34       I-3856         3.0      PORK LOIN BNLS S/CUT COVFR      1.000   
35       I-3887         3.0       PORK GROUND BRITCO PER KG      1.000   
36       I-3855         3.0                   PORK GRD FRZ       5.000   
37       I-3851         3.0       PORK BUTT BNLS 1/4 COV FR      1.000   
38       I-2311         3.0            HAM PROSCIUTTO BNLS       1.000   
39       I-2310         3.0                      HAM HONEY       6.000   
40       I-2306         3.0            HAM BLACK FOREST slc      6.000   
41       I-8260         3.0       CAPICOLLO EXT HOT CAPOLLA      1.000   
42      I-27410         3.0        BACON 3MM NATURALLY SMKD      5.000   
43       I-2308         3.0                 HAM CAPICOLLIFR      1.000   
44       I-2305         3.0                  BACON PANCETTA      1.000   
45      I-13423         3.0                   PORK STIR FRY      5.000   
46      I-19657         3.0               SAUSAGE ANDOUILLE      5.000   
47       I-2319         3.0         SMOKIES 5.5 CT BAVARIAN      1.000   
48      I-42350         3.0       PORK BACK RIB 1/2 RACK FZ      1.000   
49       I-3853         3.0              PORK CHOP 170G C/C     28.000   
50       I-8140         3.0            SAUSAGE CHORIZO WINE      1.000   
51      I-57497         3.0  SAUSAGE FRANKFURTER FLD ROAST      12.000   
52      I-22916         3.0             PORK BELLY SKON COV      1.000   
53      I-574

In [32]:
path = os.path.join(os.getcwd(), "data", "mapping", "Items_List_Assigned.csv")
Items_Assigned_Updated.to_csv(path, index = False, header = True)

## Mapping Items to Footprint Factors

In [33]:
# Map GHG footprint factors
mapping = pd.merge(Items_Assigned_Updated, ghge_factors.loc[:,['Category ID','Food Category','Active Total Supply Chain Emissions (kg CO2 / kg food)']], 
                  how = 'left',
                  left_on = 'CategoryID', 
                  right_on = 'Category ID')
for index in mapping.index:
    if np.isnan(mapping.loc[index,'Category ID']):
        mapping.loc[index,'Active Total Supply Chain Emissions (kg CO2 / kg food)'] = 0

mapping = mapping.drop(columns=['Category ID', 'Food Category'])
mapping

ItemId  CategoryID                     Description    CaseQty  \
0       I-57545         1.0         CHUCK FLAT BONELESS FZN      3.300   
1       I-10869         1.0             BEEF STIRFRY COV FR      5.000   
2        I-7064         1.0           BEEF OUTSIDE FLAT AAA      1.000   
3       I-37005         1.0                  BEEF MEATBALLS      4.540   
4       I-37002         1.0        BEEF INSIDE ROUND SHAVED      9.000   
5        I-3876         1.0           BEEF CHUCK GROUND AAA      1.000   
6       I-34065         1.0           BEEF BONES KNUCKLE FZ      1.000   
7       I-11661         1.0           BEEF STEW 3/4" FROZEN      5.000   
8        I-3837         1.0          BEEF STEW DICED 3/4"FR      1.000   
9       I-43648         1.0       BRISKET BEEF CORN SMKD FR      4.500   
10       I-3838         1.0      BEEF BRISKET BNLS 3/4" AAA      1.000   
11      I-49128         1.0       HOT DOG BEEF G/FREE 6 INC     10.000   
12      I-17055         1.0   BEEF RIB BRAISING 3 BONE 1/4"      1.000   
13      I-10775         1.0       HOT DOG BEEF 8IN 4/LB FZN     10.000   
14      I-17671         1.0    BEEF RIB-EYE SHAVED 1.5MM FZ      1.000   
15      I-20879         1.0       SOUVLAKI BEEF 75G SKEWERS      1.000   
16       I-3842         1.0          BEEF INSIDE ROUND AAA       1.000   
17       I-3846         1.0        BEEF LEAN GRD COMMERCIAL      5.000   
18       I-3867         1.0        BEEF STIRFRY MEAT FZ 1ST      5.000   
19       I-9454         1.0         BEEF BACK RIB UT COV FZ      1.000   
20      I-26667         1.0          BURGER PRIME RIB  6OZ      30.000   
21      I-28697         1.0               BURGER QUINOA YAM     60.000   
22      I-47440         1.0             JAMAICAN PATTY MILD     36.000   
23      I-47441         1.0            JAMAICAN PATTY SPICY     36.000   
24      I-13425         2.0    LAMB LEG BNLS COMMODITY AUST      1.000   
25       I-3843         2.0                      LAMB GRDFR      1.000   
26      I-43653         2.0                  LAMB STEW 3/4"     25.000   
27      I-13303         3.0            SAUSAGE PATTIES PORK      5.000   
28      I-11922         3.0       SAUSAGE MEAT CHORIZO FRZN      5.000   
29      I-50575         3.0    SAUSAGE ITAL CRUMBLE CKD FRZ      2.000   
30       I-2317         3.0    SAUSAGE FARMER DOUBLE SMOKED      1.000   
31      I-17667         3.0            SAUSAGE CHORIZO MEAT      5.000   
32       I-2333         3.0   PROSCIUTTO SLICED SAN DANIELE      1.000   
33       I-6869         3.0  PROSCIUTTO COTTO MASTRO SLICED      1.000   
34       I-3856         3.0      PORK LOIN BNLS S/CUT COVFR      1.000   
35       I-3887         3.0       PORK GROUND BRITCO PER KG      1.000   
36       I-3855         3.0                   PORK GRD FRZ       5.000   
37       I-3851         3.0       PORK BUTT BNLS 1/4 COV FR      1.000   
38       I-2311         3.0            HAM PROSCIUTTO BNLS       1.000   
39       I-2310         3.0                      HAM HONEY       6.000   
40       I-2306         3.0            HAM BLACK FOREST slc      6.000   
41       I-8260         3.0       CAPICOLLO EXT HOT CAPOLLA      1.000   
42      I-27410         3.0        BACON 3MM NATURALLY SMKD      5.000   
43       I-2308         3.0                 HAM CAPICOLLIFR      1.000   
44       I-2305         3.0                  BACON PANCETTA      1.000   
45      I-13423         3.0                   PORK STIR FRY      5.000   
46      I-19657         3.0               SAUSAGE ANDOUILLE      5.000   
47       I-2319         3.0         SMOKIES 5.5 CT BAVARIAN      1.000   
48      I-42350         3.0       PORK BACK RIB 1/2 RACK FZ      1.000   
49       I-3853         3.0              PORK CHOP 170G C/C     28.000   
50       I-8140         3.0            SAUSAGE CHORIZO WINE      1.000   
51      I-57497         3.0  SAUSAGE FRANKFURTER FLD ROAST      12.000   
52      I-22916         3.0             PORK BELLY SKON COV      1.000   
53      I-574

In [34]:
# Map nitrogen footprint factors
mapping = pd.merge(mapping, nitro_factors.loc[:,['Category ID','Food Category','g N lost/kg product']], 
                  how = 'left',
                  left_on = 'CategoryID', 
                  right_on = 'Category ID')

for index in mapping.index:
    if np.isnan(mapping.loc[index,'Category ID']):
        mapping.loc[index,'g N lost/kg product'] = 0

mapping = mapping.drop(columns=['Category ID', 'Food Category'])
mapping

ItemId  CategoryID                     Description    CaseQty  \
0       I-57545         1.0         CHUCK FLAT BONELESS FZN      3.300   
1       I-10869         1.0             BEEF STIRFRY COV FR      5.000   
2        I-7064         1.0           BEEF OUTSIDE FLAT AAA      1.000   
3       I-37005         1.0                  BEEF MEATBALLS      4.540   
4       I-37002         1.0        BEEF INSIDE ROUND SHAVED      9.000   
5        I-3876         1.0           BEEF CHUCK GROUND AAA      1.000   
6       I-34065         1.0           BEEF BONES KNUCKLE FZ      1.000   
7       I-11661         1.0           BEEF STEW 3/4" FROZEN      5.000   
8        I-3837         1.0          BEEF STEW DICED 3/4"FR      1.000   
9       I-43648         1.0       BRISKET BEEF CORN SMKD FR      4.500   
10       I-3838         1.0      BEEF BRISKET BNLS 3/4" AAA      1.000   
11      I-49128         1.0       HOT DOG BEEF G/FREE 6 INC     10.000   
12      I-17055         1.0   BEEF RIB BRAISING 3 BONE 1/4"      1.000   
13      I-10775         1.0       HOT DOG BEEF 8IN 4/LB FZN     10.000   
14      I-17671         1.0    BEEF RIB-EYE SHAVED 1.5MM FZ      1.000   
15      I-20879         1.0       SOUVLAKI BEEF 75G SKEWERS      1.000   
16       I-3842         1.0          BEEF INSIDE ROUND AAA       1.000   
17       I-3846         1.0        BEEF LEAN GRD COMMERCIAL      5.000   
18       I-3867         1.0        BEEF STIRFRY MEAT FZ 1ST      5.000   
19       I-9454         1.0         BEEF BACK RIB UT COV FZ      1.000   
20      I-26667         1.0          BURGER PRIME RIB  6OZ      30.000   
21      I-28697         1.0               BURGER QUINOA YAM     60.000   
22      I-47440         1.0             JAMAICAN PATTY MILD     36.000   
23      I-47441         1.0            JAMAICAN PATTY SPICY     36.000   
24      I-13425         2.0    LAMB LEG BNLS COMMODITY AUST      1.000   
25       I-3843         2.0                      LAMB GRDFR      1.000   
26      I-43653         2.0                  LAMB STEW 3/4"     25.000   
27      I-13303         3.0            SAUSAGE PATTIES PORK      5.000   
28      I-11922         3.0       SAUSAGE MEAT CHORIZO FRZN      5.000   
29      I-50575         3.0    SAUSAGE ITAL CRUMBLE CKD FRZ      2.000   
30       I-2317         3.0    SAUSAGE FARMER DOUBLE SMOKED      1.000   
31      I-17667         3.0            SAUSAGE CHORIZO MEAT      5.000   
32       I-2333         3.0   PROSCIUTTO SLICED SAN DANIELE      1.000   
33       I-6869         3.0  PROSCIUTTO COTTO MASTRO SLICED      1.000   
34       I-3856         3.0      PORK LOIN BNLS S/CUT COVFR      1.000   
35       I-3887         3.0       PORK GROUND BRITCO PER KG      1.000   
36       I-3855         3.0                   PORK GRD FRZ       5.000   
37       I-3851         3.0       PORK BUTT BNLS 1/4 COV FR      1.000   
38       I-2311         3.0            HAM PROSCIUTTO BNLS       1.000   
39       I-2310         3.0                      HAM HONEY       6.000   
40       I-2306         3.0            HAM BLACK FOREST slc      6.000   
41       I-8260         3.0       CAPICOLLO EXT HOT CAPOLLA      1.000   
42      I-27410         3.0        BACON 3MM NATURALLY SMKD      5.000   
43       I-2308         3.0                 HAM CAPICOLLIFR      1.000   
44       I-2305         3.0                  BACON PANCETTA      1.000   
45      I-13423         3.0                   PORK STIR FRY      5.000   
46      I-19657         3.0               SAUSAGE ANDOUILLE      5.000   
47       I-2319         3.0         SMOKIES 5.5 CT BAVARIAN      1.000   
48      I-42350         3.0       PORK BACK RIB 1/2 RACK FZ      1.000   
49       I-3853         3.0              PORK CHOP 170G C/C     28.000   
50       I-8140         3.0            SAUSAGE CHORIZO WINE      1.000   
51      I-57497         3.0  SAUSAGE FRANKFURTER FLD ROAST      12.000   
52      I-22916         3.0             PORK BELLY SKON COV      1.000   
53      I-574

In [35]:
# Map water footprint factors
mapping = pd.merge(mapping, water_factors.loc[:,['Category ID','Food Category','Freshwater Withdrawals (L/FU)', 'Stress-Weighted Water Use (L/FU)']], 
                  how = 'left',
                  left_on = 'CategoryID', 
                  right_on = 'Category ID')

for index in mapping.index:
    if np.isnan(mapping.loc[index,'Category ID']):
        mapping.loc[index,'Freshwater Withdrawals (L/FU)'] = 0
        mapping.loc[index,'Stress-Weighted Water Use (L/FU)'] = 0

mapping = mapping.drop(columns=['Category ID', 'Food Category'])
mapping.drop_duplicates(subset=["ItemId"], inplace=True)
mapping

ItemId  CategoryID                     Description    CaseQty  \
0       I-57545         1.0         CHUCK FLAT BONELESS FZN      3.300   
1       I-10869         1.0             BEEF STIRFRY COV FR      5.000   
2        I-7064         1.0           BEEF OUTSIDE FLAT AAA      1.000   
3       I-37005         1.0                  BEEF MEATBALLS      4.540   
4       I-37002         1.0        BEEF INSIDE ROUND SHAVED      9.000   
5        I-3876         1.0           BEEF CHUCK GROUND AAA      1.000   
6       I-34065         1.0           BEEF BONES KNUCKLE FZ      1.000   
7       I-11661         1.0           BEEF STEW 3/4" FROZEN      5.000   
8        I-3837         1.0          BEEF STEW DICED 3/4"FR      1.000   
9       I-43648         1.0       BRISKET BEEF CORN SMKD FR      4.500   
10       I-3838         1.0      BEEF BRISKET BNLS 3/4" AAA      1.000   
11      I-49128         1.0       HOT DOG BEEF G/FREE 6 INC     10.000   
12      I-17055         1.0   BEEF RIB BRAISING 3 BONE 1/4"      1.000   
13      I-10775         1.0       HOT DOG BEEF 8IN 4/LB FZN     10.000   
14      I-17671         1.0    BEEF RIB-EYE SHAVED 1.5MM FZ      1.000   
15      I-20879         1.0       SOUVLAKI BEEF 75G SKEWERS      1.000   
16       I-3842         1.0          BEEF INSIDE ROUND AAA       1.000   
17       I-3846         1.0        BEEF LEAN GRD COMMERCIAL      5.000   
18       I-3867         1.0        BEEF STIRFRY MEAT FZ 1ST      5.000   
19       I-9454         1.0         BEEF BACK RIB UT COV FZ      1.000   
20      I-26667         1.0          BURGER PRIME RIB  6OZ      30.000   
21      I-28697         1.0               BURGER QUINOA YAM     60.000   
22      I-47440         1.0             JAMAICAN PATTY MILD     36.000   
23      I-47441         1.0            JAMAICAN PATTY SPICY     36.000   
24      I-13425         2.0    LAMB LEG BNLS COMMODITY AUST      1.000   
25       I-3843         2.0                      LAMB GRDFR      1.000   
26      I-43653         2.0                  LAMB STEW 3/4"     25.000   
27      I-13303         3.0            SAUSAGE PATTIES PORK      5.000   
28      I-11922         3.0       SAUSAGE MEAT CHORIZO FRZN      5.000   
29      I-50575         3.0    SAUSAGE ITAL CRUMBLE CKD FRZ      2.000   
30       I-2317         3.0    SAUSAGE FARMER DOUBLE SMOKED      1.000   
31      I-17667         3.0            SAUSAGE CHORIZO MEAT      5.000   
32       I-2333         3.0   PROSCIUTTO SLICED SAN DANIELE      1.000   
33       I-6869         3.0  PROSCIUTTO COTTO MASTRO SLICED      1.000   
34       I-3856         3.0      PORK LOIN BNLS S/CUT COVFR      1.000   
35       I-3887         3.0       PORK GROUND BRITCO PER KG      1.000   
36       I-3855         3.0                   PORK GRD FRZ       5.000   
37       I-3851         3.0       PORK BUTT BNLS 1/4 COV FR      1.000   
38       I-2311         3.0            HAM PROSCIUTTO BNLS       1.000   
39       I-2310         3.0                      HAM HONEY       6.000   
40       I-2306         3.0            HAM BLACK FOREST slc      6.000   
41       I-8260         3.0       CAPICOLLO EXT HOT CAPOLLA      1.000   
42      I-27410         3.0        BACON 3MM NATURALLY SMKD      5.000   
43       I-2308         3.0                 HAM CAPICOLLIFR      1.000   
44       I-2305         3.0                  BACON PANCETTA      1.000   
45      I-13423         3.0                   PORK STIR FRY      5.000   
46      I-19657         3.0               SAUSAGE ANDOUILLE      5.000   
47       I-2319         3.0         SMOKIES 5.5 CT BAVARIAN      1.000   
48      I-42350         3.0       PORK BACK RIB 1/2 RACK FZ      1.000   
49       I-3853         3.0              PORK CHOP 170G C/C     28.000   
50       I-8140         3.0            SAUSAGE CHORIZO WINE      1.000   
51      I-57497         3.0  SAUSAGE FRANKFURTER FLD ROAST      12.000   
52      I-22916         3.0             PORK BELLY SKON COV      1.000   
53      I-574

In [36]:
mapping[mapping["ItemId"] == "I-4524"]

ItemId  CategoryID   Description  CaseQty CaseUOM  PakQty PakUOM  \
2006  I-4524        38.0  BEETS GOLDBC      5.0      lb     1.0     lb   

     InventoryGroup  Active Total Supply Chain Emissions (kg CO2 / kg food)  \
2006        PRODUCE                                             0.3062        

      g N lost/kg product  Freshwater Withdrawals (L/FU)  \
2006                  7.9                            9.9   

      Stress-Weighted Water Use (L/FU)  
2006                              37.9

In [37]:
mapping["CategoryID"].isnull().sum()

0

### Manully Adjust Footprint Factor for Specific Items

In [38]:
for index, row in Manual_Factor.iterrows():
    itemId = Manual_Factor.loc[index, 'ItemId']
    ghge = Manual_Factor.loc[index, 'Active Total Supply Chain Emissions (kg CO2 / kg food)']
    nitro = Manual_Factor.loc[index, 'g N lost/kg product']
    water = Manual_Factor.loc[index, 'Freshwater Withdrawals (L/FU)']
    str_water = Manual_Factor.loc[index, 'Stress-Weighted Water Use (L/FU)']
    mapping.loc[mapping['ItemId'] == itemId, 'Active Total Supply Chain Emissions (kg CO2 / kg food)'] = ghge
    mapping.loc[mapping['ItemId'] == itemId, 'g N lost/kg product'] = nitro
    mapping.loc[mapping['ItemId'] == itemId, 'Freshwater Withdrawals (L/FU)'] = water
    mapping.loc[mapping['ItemId'] == itemId, 'Stress-Weighted Water Use (L/FU)'] = str_water

In [39]:
mapping.drop_duplicates(subset = ['ItemId'], inplace=True)
mapping.dtypes

ItemId                                                     object
CategoryID                                                float64
Description                                                object
CaseQty                                                   float64
CaseUOM                                                    object
PakQty                                                    float64
PakUOM                                                     object
InventoryGroup                                             object
Active Total Supply Chain Emissions (kg CO2 / kg food)    float64
g N lost/kg product                                       float64
Freshwater Withdrawals (L/FU)                             float64
Stress-Weighted Water Use (L/FU)                          float64
dtype: object

In [40]:
mapping.shape

(2077, 12)

In [41]:
mapping

ItemId  CategoryID                     Description    CaseQty  \
0       I-57545         1.0         CHUCK FLAT BONELESS FZN      3.300   
1       I-10869         1.0             BEEF STIRFRY COV FR      5.000   
2        I-7064         1.0           BEEF OUTSIDE FLAT AAA      1.000   
3       I-37005         1.0                  BEEF MEATBALLS      4.540   
4       I-37002         1.0        BEEF INSIDE ROUND SHAVED      9.000   
5        I-3876         1.0           BEEF CHUCK GROUND AAA      1.000   
6       I-34065         1.0           BEEF BONES KNUCKLE FZ      1.000   
7       I-11661         1.0           BEEF STEW 3/4" FROZEN      5.000   
8        I-3837         1.0          BEEF STEW DICED 3/4"FR      1.000   
9       I-43648         1.0       BRISKET BEEF CORN SMKD FR      4.500   
10       I-3838         1.0      BEEF BRISKET BNLS 3/4" AAA      1.000   
11      I-49128         1.0       HOT DOG BEEF G/FREE 6 INC     10.000   
12      I-17055         1.0   BEEF RIB BRAISING 3 BONE 1/4"      1.000   
13      I-10775         1.0       HOT DOG BEEF 8IN 4/LB FZN     10.000   
14      I-17671         1.0    BEEF RIB-EYE SHAVED 1.5MM FZ      1.000   
15      I-20879         1.0       SOUVLAKI BEEF 75G SKEWERS      1.000   
16       I-3842         1.0          BEEF INSIDE ROUND AAA       1.000   
17       I-3846         1.0        BEEF LEAN GRD COMMERCIAL      5.000   
18       I-3867         1.0        BEEF STIRFRY MEAT FZ 1ST      5.000   
19       I-9454         1.0         BEEF BACK RIB UT COV FZ      1.000   
20      I-26667         1.0          BURGER PRIME RIB  6OZ      30.000   
21      I-28697         1.0               BURGER QUINOA YAM     60.000   
22      I-47440         1.0             JAMAICAN PATTY MILD     36.000   
23      I-47441         1.0            JAMAICAN PATTY SPICY     36.000   
24      I-13425         2.0    LAMB LEG BNLS COMMODITY AUST      1.000   
25       I-3843         2.0                      LAMB GRDFR      1.000   
26      I-43653         2.0                  LAMB STEW 3/4"     25.000   
27      I-13303         3.0            SAUSAGE PATTIES PORK      5.000   
28      I-11922         3.0       SAUSAGE MEAT CHORIZO FRZN      5.000   
29      I-50575         3.0    SAUSAGE ITAL CRUMBLE CKD FRZ      2.000   
30       I-2317         3.0    SAUSAGE FARMER DOUBLE SMOKED      1.000   
31      I-17667         3.0            SAUSAGE CHORIZO MEAT      5.000   
32       I-2333         3.0   PROSCIUTTO SLICED SAN DANIELE      1.000   
33       I-6869         3.0  PROSCIUTTO COTTO MASTRO SLICED      1.000   
34       I-3856         3.0      PORK LOIN BNLS S/CUT COVFR      1.000   
35       I-3887         3.0       PORK GROUND BRITCO PER KG      1.000   
36       I-3855         3.0                   PORK GRD FRZ       5.000   
37       I-3851         3.0       PORK BUTT BNLS 1/4 COV FR      1.000   
38       I-2311         3.0            HAM PROSCIUTTO BNLS       1.000   
39       I-2310         3.0                      HAM HONEY       6.000   
40       I-2306         3.0            HAM BLACK FOREST slc      6.000   
41       I-8260         3.0       CAPICOLLO EXT HOT CAPOLLA      1.000   
42      I-27410         3.0        BACON 3MM NATURALLY SMKD      5.000   
43       I-2308         3.0                 HAM CAPICOLLIFR      1.000   
44       I-2305         3.0                  BACON PANCETTA      1.000   
45      I-13423         3.0                   PORK STIR FRY      5.000   
46      I-19657         3.0               SAUSAGE ANDOUILLE      5.000   
47       I-2319         3.0         SMOKIES 5.5 CT BAVARIAN      1.000   
48      I-42350         3.0       PORK BACK RIB 1/2 RACK FZ      1.000   
49       I-3853         3.0              PORK CHOP 170G C/C     28.000   
50       I-8140         3.0            SAUSAGE CHORIZO WINE      1.000   
51      I-57497         3.0  SAUSAGE FRANKFURTER FLD ROAST      12.000   
52      I-22916         3.0             PORK BELLY SKON COV      1.000   
53      I-574

In [42]:
ingredients = pd.read_csv("data/preprocessed/Ingredients_List.csv")
ingredients

IngredientId       Qty    Uom   Conversion  InvFactor   Recipe
0          I-3643   225.000      g     0.001000     0.1837  P-18907
1          I-6026  1000.000      g     1.000000     0.8163  P-18907
2          I-3642     1.000     Kg  1000.000000     0.0002  P-25993
3          I-6026     5.000     Kg  1000.000000     0.0008  P-25993
4          I-1813   125.000     ml     0.033814    37.8788  P-26044
5          I-2612     2.250     Kg     1.000000     0.6818  P-26044
6          I-3284    10.000     ml     0.002000     3.0303  P-26044
7          I-3660   250.000      g     0.001000    75.7576  P-26044
8          I-5983   625.000     ml     0.001000   189.3939  P-26044
9          I-6820    60.000      g     0.001000    18.1818  P-26044
10         I-2156     1.000     Kg     1.000000     0.0012  P-26055
11        P-18907     5.000      g     1.000000     0.0059  P-26055
12         I-2159     1.000     CT     1.000000     1.0000  P-26057
13         I-3388     2.000     ml     0.001000     2.0000  P-26057
14        P-18907     0.250      g     1.000000     0.2500  P-26057
15         I-1813   250.000     ml     0.033814   250.0000  P-26058
16         I-3388   750.000     ml     0.001000   750.0000  P-26058
17         I-1813   125.000     ml     0.033814    48.0769  P-26063
18         I-3284    30.000     ml     0.002000    11.5385  P-26063
19         I-3660   325.000      g     0.001000   125.0000  P-26063
20         I-4531     1.800     Kg     2.204620     0.6923  P-26063
21         I-5983   250.000     ml     0.001000    96.1538  P-26063
22        P-50495   125.000     ml     0.001000    48.0769  P-26063
23         I-4463    10.000      g     0.002205     0.6667  P-26069
24        P-18907     0.100      g     1.000000     0.0067  P-26069
25        P-26058     5.000     ml     0.001000     0.3333  P-26069
26         I-4725     2.250     Kg     2.204620     2.0018  P-26205
27         I-6006   100.000     ml     0.001000    88.9680  P-26205
28        P-25993     5.000      g     1.000000     4.4484  P-26205
29         I-3360     2.000     Kg     1.000000     0.4167  P-28285
30         I-5983     2.800      L     1.000000     0.5833  P-28285
31         I-3223     2.840      L     1.000000     0.9161  P-32739
32         I-3284    20.000     ml     0.002000     6.4516  P-32739
33         I-3660   250.000      g     0.001000    80.6452  P-32739
34        I-14773   800.000      g     0.001000   200.0000  P-34892
35         I-5983     3.000      L     1.000000     0.7500  P-34892
36         I-8060     1.360     Kg  1000.000000     0.3400  P-34892
37         I-2159     1.000     CT     1.000000     1.0000  P-44587
38         I-3386     2.000     ml     0.001000     2.0000  P-44587
39        P-18907     0.250      g     1.000000     0.2500  P-44587
40        I-17667     5.000     Kg     1.000000     1.4286  P-44592
41         I-4472     7.000     CT     1.000000     4.3750  P-44913
42         I-4973   900.000      g     1.000000   562.5000  P-44913
43         I-6443    45.000     ml     0.033814    28.1250  P-44913
44        P-18907     5.000      g     1.000000     3.1250  P-44913
45        I-27410     5.000     Kg     1.000000     2.8571  P-46076
46        I-35791   454.000      g     1.000000    22.7000  P-46862
47         I-3360     2.000     Kg     1.000000     0.4000  P-50310
48         I-3471   400.000      g     0.001000    80.0000  P-50310
49         I-3625    15.000      g     1.000000     3.0000  P-50310
50         I-3638     5.000      g     1.000000     1.0000  P-50310
51         I-5983     2.775      L     1.000000     0.5550  P-50310
52         P-9714   500.000      g     0.001000   100.0000  P-50310
53         I-2117     1.000     Kg     1.000000     0.8333  P-50316
54         I-2251   250.000     ml     0.001000   208.3333  P-50316
55         I-3661    60.000      g     0.001000    50.0000  P-50316
56         I-1813   400.000     ml     0.033814    80.0000  P-50317
57         I-3360     2.000     Kg     1.000000     0.4000  P

In [43]:
map_list = mapping["ItemId"].unique()
absent_list = []

for item in ingredients["IngredientId"].unique():
    if item not in map_list:
        absent_list.append(item)
        
print(absent_list)

['P-18907', 'P-50495', 'P-26058', 'P-25993', 'P-9714', 'P-9713', 'P-28285', 'P-50598', 'P-58949', 'P-26055', 'P-26069', 'P-34892', 'P-44592', 'P-50310', 'P-50316', 'P-50317', 'P-26057', 'P-46862', 'R-30406', 'P-32739', 'P-50739', 'P-50636', 'P-50337', 'P-26205', 'P-44587', 'P-44913', 'P-46076', 'P-26063', 'P-26044', 'P-50513', 'P-48933', 'P-26514', 'P-52036', 'P-26020', 'P-44896', 'P-29315', 'P-34085', 'P-26077', 'P-48489', 'P-26231', 'P-32661', 'P-38556', 'P-58359', 'P-26090', 'P-26460', 'P-41095', 'P-34123', 'P-34880', 'P-42499', 'P-44728', 'P-46869', 'P-50583', 'P-50584', 'P-7444', 'P-26196', 'P-41096', 'P-9741', 'P-9765', 'P-24452', 'P-57146', 'P-19175', 'P-50587', 'P-34534', 'P-50429', 'P-51536', 'P-6888', 'P-8196', 'P-22247', 'P-44652', 'P-21077', 'P-41468', 'P-41466', 'P-57227', 'P-46492', 'P-48870', 'P-57214', 'P-24750', 'P-43440', 'P-10113', 'P-51582', 'P-56459', 'P-9710', 'P-9712', 'P-56887', 'P-9745', 'P-39167', 'P-41094', 'P-56741', 'P-15353', 'P-33557', 'P-53277', 'P-22534

In [44]:
path = os.path.join(os.getcwd(), "data", "mapping", "Mapping.csv")
mapping.to_csv(path, index = False, header = True)